<a href="https://colab.research.google.com/github/HiYongg/mask_detect/blob/main/maskcheck.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import os
from datetime import datetime
import time
from PIL import Image
import numpy as np
import cv2
from google.colab.patches import cv2_imshow
import matplotlib.pyplot as plt


filelist=[] 
#디렉토리 이름을 주면, 그 디렉토리에 포함된 모든 파일명의 리스트
def search(filelist, dirname):
    filenames = os.listdir(dirname)
    for filename in filenames:
        full_filename = os.path.join(dirname, filename)
        filelist.append((full_filename,filename))

# 얻어온 파일 리스트에서 'no'가 포함되어 있는 파일을 0, 'no'가 없는 파일을 1로 구분해서 넘파이 배열로 저장

for name in filelist:
    full_filename, filename = name    
    if "jpg" in filename:
      # 이미지 열기
      img = cv2.imread(full_filename, cv2.IMREAD_COLOR)
      img = cv2.resize(img, dsize=(imgsize,imgsize), interpolation=cv2.INTER_AREA)
      X.append(img/256)
      if "no" in filename:
          Y.append(0)
      else:
          Y.append(1)
train_images = np.array(X)
y = np.array(Y)
train_labels = y.reshape(-1,1)
#train_labels = y

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dropout, Activation, Dense, BatchNormalization, GlobalAveragePooling2D
from tensorflow.keras.layers import Flatten, Convolution2D, MaxPooling2D, Conv2D
from tensorflow.keras.models import load_model
from tensorflow.keras.optimizers import Adam
import os, re, glob
import cv2
import numpy as np
import os
from datetime import datetime
import time
from PIL import Image
import numpy as np
import cv2
#from google.colab.patches import cv2_imshow
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.model_selection import train_test_split
import tensorflow as tf

path = '/content/drive/MyDrive/totalmask'
umumask = ['nomask','mask']

num_classes = 2


X = []
Y = []

for idex, umu in enumerate(umumask):

    image_dir = path+'/'+ umu + '/'

    for top, dir, f in os.walk(image_dir):
        for filename in f:
            img = cv2.imread(image_dir + filename,cv2.IMREAD_COLOR)
            img = cv2.resize(img, dsize=(256,256), interpolation=cv2.INTER_AREA)
            #print(img.shape)
            X.append(img / 256)
            Y.append(idex)

path2 = '/content/drive/MyDrive/train_data'

for idex, umu in enumerate(umumask):

    image_dir = path2+'/'+ umu + '/'

    for top, dir, f in os.walk(image_dir):
        for filename in f:
            img = cv2.imread(image_dir + filename,cv2.IMREAD_COLOR)
            img = cv2.resize(img, dsize=(256,256), interpolation=cv2.INTER_AREA)
            #print(img.shape)
            X.append(img / 256)
            Y.append(idex)

path2 = '/content/drive/MyDrive/sideface'

for idex, umu in enumerate(umumask):

    image_dir = path2+'/'+ umu + '/'

    for top, dir, f in os.walk(image_dir):
        for filename in f:
            img = cv2.imread(image_dir + filename,cv2.IMREAD_COLOR)
            img = cv2.resize(img, dsize=(256,256), interpolation=cv2.INTER_AREA)
            #print(img.shape)
            X.append(img / 256)
            Y.append(idex)

#mask=pd.DataFrame((X,Y),columns=['sample','OX'])

train_images = np.array(X)
y = np.array(Y)
train_labels = y.reshape(-1,1)
#print(X)
#print(Y)

In [ ]:
train_images.shape

(1541, 256, 256, 3)

In [ ]:
import tensorflow as tf
X_train, X_test,y_train, y_test =train_test_split(train_images,train_labels,random_state=0)



In [ ]:
print(X_test.shape)
X_train.shape


(386, 256, 256, 3)


(1155, 256, 256, 3)

In [ ]:
#alexnet
model=Sequential([
    Conv2D(96, (11, 11), strides=4, padding='valid', input_shape = (227,227, 3)),
    MaxPooling2D((3,3),2),
    BatchNormalization(),

    Conv2D(256,(3,3),activation='relu',padding='same'),
    MaxPooling2D((3, 3), 2),
    BatchNormalization(),

    Conv2D(384, (3, 3), activation='relu', padding='same'),
    Conv2D(384,(3,3),activation='relu',padding='same'),
    Conv2D(384,(3,3),activation='relu',padding='same'),
    MaxPooling2D((3, 3), 2),
    Flatten(),

    Dense(1024, activation='relu'),
    Dropout(0.5),
    Dense(512,activation='relu'),
    Dropout(0.5),
    Dense(2,activation='softmax'),
])

model.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

model.fit(X_train,y_train,epochs=30)
#model.fit(X_train,y_train,epochs=10)



In [ ]:
#
model7=Sequential([
    Conv2D(128,(8,8),strides=4,activation='relu', input_shape=(256,256,3)),
    MaxPooling2D((4,4),strides=2,padding='same'),
    Dropout(0.25),

    Conv2D(384,(3,3),activation='relu'),
    MaxPooling2D((4,4),strides=2,padding='same'),
    Dropout(0.25),

    Conv2D(384,(3,3),activation='relu'),
    MaxPooling2D((4,4),strides=2,padding='same'),
    Dropout(0.25),

    Flatten(),
    Dense(256,activation='relu'),
    Dropout(0.5),
    Dense(2,activation='softmax'),
])

model7.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])


model7.fit(train_images,train_labels,epochs=50,batch_size=32)
#model7.fit(X_train,y_train,epochs=30,batch_size=32)
#model.fit(X_train,y_train,epochs=10)

#model0 첫번째conv2d size(4,4) train 0.90 test0.84 input_shape=64 128 227 256
#model0 첫번째conv2d size(4,4) train 0.90 test0.84 --> 검은 마스크 인식 잘 안됨. --> 검은색 마스크 추가
#model1 첫번째conv2d size(4,4) train 0.97 test0.94 -->마스크 쓰고 옆모습 인식이 잘 안됨 256train097test094.h5
#model2 첫번째 conv2 size(8,8) train 0.97 test0.939 -->여전히 옆모습 인식 x
#model3 구조들은 그대로 테스트데이터에 옆모습 추가 train0.979 test0.89 --> 오히려 정확도 줄어듬 --> 코스크를 마스큰 쓴 것으로 인식하는 문제 생김
#model4 튀는 데이터들 골라 내기 --> 정화도는 좀 올랐지만 코스크 해결 안됨
#model5 maxpooling 후 dropout 0.2 추가하기 \ epochs=25 model5_256train092test091
#model6 batch size=32 추가 
#now best model is model6

#model7 dropout 0.25


Epoch 1/50


/usr/local/lib/python3.7/dist-packages/tensorflow/python/util/dispatch.py:1082: UserWarning: "`sparse_categorical_crossentropy` received `from_logits=True`, but the `output` argument was produced by a sigmoid or softmax activation and thus does not represent logits. Was this intended?"
  return dispatch_target(*args, **kwargs)


49/49 [==============================] - 146s 3s/step - loss: 0.8076 - accuracy: 0.5425
Epoch 2/50
49/49 [==============================] - 146s 3s/step - loss: 0.5160 - accuracy: 0.7236
Epoch 3/50
49/49 [==============================] - 147s 3s/step - loss: 0.3894 - accuracy: 0.8014
Epoch 4/50
49/49 [==============================] - 149s 3s/step - loss: 0.3679 - accuracy: 0.8144
Epoch 5/50
49/49 [==============================] - 146s 3s/step - loss: 0.3500 - accuracy: 0.8177
Epoch 6/50
49/49 [==============================] - 145s 3s/step - loss: 0.3529 - accuracy: 0.8293
Epoch 7/50
49/49 [==============================] - 147s 3s/step - loss: 0.3496 - accuracy: 0.8170
Epoch 8/50
49/49 [==============================] - 147s 3s/step - loss: 0.3109 - accuracy: 0.8456
Epoch 9/50
49/49 [==============================] - 147s 3s/step - loss: 0.3514 - accuracy: 0.8157
Epoch 10/50
49/49 [==============================] - 146s 3s/step - loss: 0.2992 - accuracy: 0.8566
Epoch 11/50
49/49 [=

KeyboardInterrupt: ignored

In [ ]:
model7.fit(train_images,train_labels,epochs=20,batch_size=32)

Epoch 1/20
49/49 [==============================] - 144s 3s/step - loss: 0.1286 - accuracy: 0.9435
Epoch 2/20
49/49 [==============================] - 147s 3s/step - loss: 0.1499 - accuracy: 0.9390
Epoch 3/20
49/49 [==============================] - 144s 3s/step - loss: 0.1283 - accuracy: 0.9468
Epoch 4/20
49/49 [==============================] - 147s 3s/step - loss: 0.1236 - accuracy: 0.9474
Epoch 5/20
49/49 [==============================] - 143s 3s/step - loss: 0.1722 - accuracy: 0.9254
Epoch 6/20
49/49 [==============================] - 144s 3s/step - loss: 0.1157 - accuracy: 0.9513
Epoch 7/20
49/49 [==============================] - 144s 3s/step - loss: 0.1480 - accuracy: 0.9332
Epoch 8/20
49/49 [==============================] - 143s 3s/step - loss: 0.1404 - accuracy: 0.9364
Epoch 9/20
49/49 [==============================] - 145s 3s/step - loss: 0.1102 - accuracy: 0.9565
Epoch 10/20
49/49 [==============================] - 143s 3s/step - loss: 0.1103 - accuracy: 0.9572
Epoch 11/

In [ ]:
model=load_model('/content/drive/MyDrive/227train098test091.h5')

In [ ]:
model.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])



In [ ]:
model.fit(X_train,y_train,epochs=10)

Epoch 1/5
36/36 [==============================] - 36s 986ms/step - loss: 0.0639 - accuracy: 0.9770
Epoch 2/5
36/36 [==============================] - 34s 939ms/step - loss: 0.0801 - accuracy: 0.9788
Epoch 3/5
36/36 [==============================] - 34s 951ms/step - loss: 0.0524 - accuracy: 0.9770
Epoch 4/5
36/36 [==============================] - 36s 999ms/step - loss: 0.0663 - accuracy: 0.9814
Epoch 5/5
36/36 [==============================] - 34s 954ms/step - loss: 0.1256 - accuracy: 0.9593


In [ ]:
model7.save('/content/drive/MyDrive/model7_test095.h5')

In [ ]:
test_loss, test_acc=model6.evaluate(X_test, y_test, verbose=2)
print('\nTest accuracy:',test_acc)



13/13 - 9s - loss: 0.2521 - accuracy: 0.9147 - 9s/epoch - 725ms/step

Test accuracy: 0.9147287011146545


In [ ]:
predicted_result = model6.predict(X_test)
predicted_labels = np.argmax(predicted_result, axis=1)
test_labels_list = y_test

wrong_result = []
for n in range(0, len(y_test)):
    if predicted_labels[n] != test_labels_list[n]:
        wrong_result.append(n)

#samples = random.sample(population=wrong_result, k=16)

count = 0
ncols = 3
mod = divmod(len(wrong_result),ncols)
nrows = mod[0] + mod[1]
plt.figure(figsize=(300,300))
for n in wrong_result:
    count = count + 1
    plt.subplot(nrows, ncols, count)
    plt.imshow(X_test[n].reshape(256, 256,3), interpolation='nearest')
    tmp = "Label:" + str(test_labels_list[n]) + ", Prediction:" + str(predicted_labels[n])
    plt.title(tmp,fontsize=10)

plt.tight_layout()
plt.show()